# 20200624 Calosaturnia revbayes molecular dating

Based on tutorial: https://revbayes.github.io/tutorials/dating/

In [2]:
aln <- readDiscreteCharacterData("renamed_20180914_Calosaturnia_COI3P5P.nex")

n_taxa <- aln.size()
taxa <- aln.taxa()

   Successfully read one character matrix from file 'renamed_20180914_Calosaturnia_COI3P5P.nex'


In [3]:
print(taxa)

cjo02_Calosaturnia_spn,cjo03_Calosaturnia_walterorum,cjo15_Calosaturnia_walterorum,cjo21_Calosaturnia_albofasciata,cjo25_Calosaturnia_albofasciata,cjo26_Calosaturnia_spn,cjo27_Calosaturnia_mendocino,cjo28_Calosaturnia_mendocino,dn2234_Calosaturnia_albofasciata,dn2235_Calosaturnia_albofasciata,dn2236_Calosaturnia_albofasciata,dn2237_Calosaturnia_albofasciata,dn2658_Calosaturnia_walterorum,dn2659_Calosaturnia_walterorum,dn2660_Calosaturnia_walterorum,dn2661_Calosaturnia_walterorum,dn2665_Calosaturnia_spn,dn2666_Calosaturnia_spn,dn2675_Calosaturnia_spn,dn2676_Calosaturnia_spn,dn2677_Calosaturnia_spn,dn2678_Calosaturnia_spn,dn2679_Calosaturnia_spn,dn2680_Calosaturnia_spn,dn2681_Calosaturnia_spn,dn2682_Calosaturnia_spn,dn2683_Calosaturnia_spn,dn2684_Calosaturnia_spn,dn2685_Calosaturnia_spn,dn2686_Calosaturnia_spn,jbt01_Calosaturnia_walterorum,jbt02_Calosaturnia_walterorum,jbt03_Calosaturnia_walterorum,jbt04_Calosaturnia_walterorum,jbt05_Calosaturnia_mendocino,jbt06_Calosaturnia_spn,jbt07_Ca

In [4]:
moves = VectorMoves()
monitors = VectorMonitors()

Set up birth-death tree model. Vectors constant over time and drawn indepently from a exponential distribution

In [5]:
speciation_rate ~ dnExponential(10)
extinction_rate ~ dnExponential(10)

moves.append( mvScale(speciation_rate, lambda=0.5, tune=true, weight=3.0) )
moves.append( mvScale(extinction_rate, lambda=0.5, tune=true, weight=3.0) )

Diversification and turnover rates

In [6]:
diversification := speciation_rate - extinction_rate
turnover := extinction_rate/speciation_rate

Set proportion of extant taxa sampled

In [7]:
rho <- 1.0

Set root age. Either fixed or uniform distribution, dnBDP does not accept normal distribution.

In [8]:
#extant_mrca <- 18.5

extant_mrca ~ dnUniform(14.5, 22) # min, max

Define prior distribution on tree topology and divergence times

In [9]:
tree_dist = dnBDP(lambda=speciation_rate, mu=extinction_rate, rho=rho, rootAge=extant_mrca, samplingStrategy="uniform", condition="nTaxa", taxa=taxa)

In [10]:
outgroup = clade("jbt39_Agapema_anona", "jbt21_Agapema_homogena")

clade_mendo = clade("cjo27_Calosaturnia_mendocino",
"cjo28_Calosaturnia_mendocino",
"jbt05_Calosaturnia_mendocino",
"jbt07_Calosaturnia_mendocino",
"jbt08_Calosaturnia_mendocino",
"jbt12_Calosaturnia_mendocino",
"jbt18_Calosaturnia_mendocino",
"jbt27_Calosaturnia_mendocino",
"jbt28_Calosaturnia_mendocino",
"jbt29_Calosaturnia_mendocino",
"jbt30_Calosaturnia_mendocino",
"jbt31_Calosaturnia_mendocino",
"jbt33_Calosaturnia_mendocino",
"jbt36_Calosaturnia_mendocino",
"jbt37_Calosaturnia_mendocino",
"jw40_Calosaturnia_mendocino",
"jw42_Calosaturnia_mendocino",
"jw43_Calosaturnia_mendocino",
"jw44_Calosaturnia_mendocino",
"tl01_Calosaturnia_mendocino",
"tl08_Calosaturnia_mendocino")

clade_albo = clade("cjo21_Calosaturnia_albofasciata",
"cjo25_Calosaturnia_albofasciata",
"dn2234_Calosaturnia_albofasciata",
"dn2235_Calosaturnia_albofasciata",
"dn2236_Calosaturnia_albofasciata",
"dn2237_Calosaturnia_albofasciata",
"jbt13_Calosaturnia_albofasciata",
"jbt15_Calosaturnia_albofasciata",
"jbt16_Calosaturnia_albofasciata",
"jbt22_Calosaturnia_albofasciata",
"jbt34_Calosaturnia_albofasciata",
"jbt35_Calosaturnia_albofasciata",
"jw35_Calosaturnia_albofasciata",
"jw36_Calosaturnia_albofasciata",
"jw38_Calosaturnia_albofasciata",
"jw45_Calosaturnia_albofasciata",
"jw46_Calosaturnia_albofasciata",
"jw48_Calosaturnia_albofasciata",
"jw49_Calosaturnia_albofasciata",
"jw50_Calosaturnia_albofasciata",
"jw51_Calosaturnia_albofasciata")

constraints = v(clade_mendo, clade_albo, outgroup)

timetree ~ dnConstrainedTopology(tree_dist, constraints=constraints)

Calibrate split between C. albofasciata and other ingroups around 11.3 Ma

In [11]:
age_albo := tmrca(timetree, clade_albo)
#obs_age_albo ~ dnExponential(1.0, offset = -age_albo)
obs_age_albo ~ dnNormal(-age_albo, 4)
obs_age_albo.clamp(-11.3)

In [12]:
age_mendo := tmrca(timetree, clade_mendo)
#obs_age_mendo ~ dnExponential(1.0, offset = -age_albo)
obs_age_mendo ~ dnNormal(-age_mendo, 1.5)
obs_age_mendo.clamp(-3.2)

In [13]:
moves.append( mvNarrow(timetree, weight=n_taxa) )
moves.append( mvFNPR(timetree, weight=n_taxa/4) )
moves.append( mvNodeTimeSlideUniform(timetree, weight=n_taxa) )
moves.append( mvSubtreeScale(timetree, weight=n_taxa/5.0) )

Set up a global molecular clock model

In [14]:
branch_rates ~ dnExponential(10.0)
moves.append( mvScale(branch_rates, lambda=0.5, tune=true, weight=3.0) )

Set up GTR+G substitution model

In [15]:
sf_hp <- v(1,1,1,1)
sf ~ dnDirichlet(sf_hp)

er_hp <- v(1,1,1,1,1,1)
er ~ dnDirichlet(er_hp)

moves.append( mvBetaSimplex(er, alpha=10.0, weight=3.0) )
moves.append( mvBetaSimplex(sf, alpha=10.0, weight=2.0) )

Q_aln := fnGTR(er,sf)

alpha_aln ~ dnUniform(0,1E7)
alpha_aln.setValue( 1.0 )
moves.append( mvScale(alpha_aln))

rates_aln := fnDiscretizeGamma(alpha_aln, alpha_aln, 4)

phySeq ~ dnPhyloCTMC(tree=timetree, Q=Q_aln, siteRates=rates_aln, branchRates=branch_rates, type="DNA")
phySeq.clamp(aln)

Run MCMC

In [16]:
mymodel = model(sf)
monitors.append( mnModel(filename="20200619_Calosaturnia1.log", printgen=10) )
monitors.append( mnFile(filename="20200619_Calosaturnia1.trees", printgen=10, timetree) )
monitors.append( mnScreen(printgen=10, extant_mrca, diversification, branch_rates) )
mymcmc = mcmc(mymodel, monitors, moves, nruns=2, combine="mixed")
mymcmc.run(generations=20000, tuningInterval=200)
trace = readTreeTrace("20200619_Calosaturnia1.trees")
mccTree(trace, file="20200619_Calosaturnia1.mcc.tre")



   Running MCMC simulation
   This simulation runs 2 independent replicates.
   The simulator uses 10 different moves in a random move schedule with 233.05 moves per iteration

Iter        |      Posterior   |     Likelihood   |          Prior   |   branch_rates   |   diversific..   |    extant_mrca   |    elapsed   |        ETA   |
-------------------------------------------------------------------------------------------------------------------------------------------------------------
0           |       -12780.1   |       -12288.4   |       -491.739   |     0.01613367   |     0.04134127   |       16.82107   |   00:00:00   |   --:--:--   |
10          |       -6272.52   |       -5899.42   |       -373.103   |    0.006293972   |      0.5293852   |       16.82107   |   00:00:07   |   --:--:--   |
20          |       -5149.95   |       -4802.05   |       -347.902   |    0.004988926   |      0.8896629   |       16.82107   |   00:00:14   |   03:53:06   |
30          |        -4979.3   |

440         |       -4706.31   |       -4391.68   |       -314.631   |    0.005348221   |      0.7438575   |       16.82107   |   00:04:39   |   03:26:42   |
450         |       -4706.16   |       -4390.07   |       -316.088   |    0.004638033   |      0.5335098   |       16.82107   |   00:04:46   |   03:27:05   |
460         |       -4713.54   |       -4391.88   |       -321.663   |    0.004397252   |      0.6476868   |       16.82107   |   00:04:52   |   03:26:43   |
470         |        -4710.1   |       -4385.53   |       -324.576   |    0.004435819   |      -0.526478   |       16.82107   |   00:04:59   |   03:27:04   |
480         |       -4711.28   |       -4384.98   |         -326.3   |    0.003917647   |      0.4075416   |       16.82107   |   00:05:05   |   03:26:43   |
490         |       -4709.73   |       -4386.29   |       -323.438   |    0.004147998   |      0.5117729   |       16.82107   |   00:05:12   |   03:27:02   |
500         |       -4704.67   |       -4383.97   | 

910         |       -4709.34   |       -4388.61   |       -320.734   |    0.004239285   |      0.6306007   |       16.82107   |   00:09:31   |   03:19:38   |
920         |       -4711.52   |       -4390.43   |       -321.094   |    0.004592091   |     -0.7456188   |       16.82107   |   00:09:37   |   03:19:26   |
930         |       -4720.17   |       -4396.09   |       -324.087   |    0.004296681   |      -1.022004   |       16.82107   |   00:09:43   |   03:19:14   |
940         |        -4708.3   |       -4390.34   |       -317.964   |     0.00453004   |     -0.8127535   |       16.82107   |   00:09:51   |   03:19:43   |
950         |       -4706.97   |       -4391.47   |       -315.496   |    0.004935178   |      -1.478743   |       16.82107   |   00:09:58   |   03:19:51   |
960         |       -4691.27   |       -4381.18   |       -310.087   |    0.005320862   |     -0.9633251   |       16.82107   |   00:10:04   |   03:19:39   |
970         |       -4708.63   |       -4389.13   | 

1380        |       -4731.43   |       -4403.49   |       -327.933   |    0.004307135   |      -1.402217   |       16.82107   |   00:14:41   |   03:18:07   |
1390        |       -4716.43   |       -4394.39   |       -322.037   |     0.00429503   |      -1.038343   |       16.82107   |   00:14:47   |   03:17:55   |


Iter        |      Posterior   |     Likelihood   |          Prior   |   branch_rates   |   diversific..   |    extant_mrca   |    elapsed   |        ETA   |
-------------------------------------------------------------------------------------------------------------------------------------------------------------
1400        |       -4701.27   |       -4385.42   |       -315.857   |    0.004815915   |      0.3651413   |       16.82107   |   00:14:54   |   03:17:57   |
1410        |       -4708.96   |       -4396.43   |       -312.524   |    0.005158714   |       0.594737   |       16.82107   |   00:15:00   |   03:17:45   |
1420        |       -4689.46   |        -4374.5   

1830        |       -4724.55   |       -4400.14   |       -324.415   |    0.004031281   |       0.686083   |       16.82107   |   00:19:32   |   03:13:56   |
1840        |       -4697.63   |       -4375.96   |       -321.669   |    0.004765404   |      0.5719163   |       16.82107   |   00:19:39   |   03:13:56   |
1850        |       -4706.03   |       -4388.75   |       -317.284   |    0.004492951   |     -0.6535684   |       16.82107   |   00:19:45   |   03:13:45   |
1860        |       -4712.83   |       -4387.79   |       -325.038   |    0.004473163   |     0.02795571   |       16.82107   |   00:19:51   |   03:13:35   |
1870        |       -4709.02   |       -4388.44   |       -320.579   |    0.004285783   |       0.523134   |       16.82107   |   00:19:57   |   03:13:25   |
1880        |       -4721.03   |       -4391.55   |       -329.478   |    0.003622034   |      0.4613272   |       16.82107   |   00:20:03   |   03:13:14   |
1890        |        -4709.4   |       -4388.12   | 

...

18060       |       -4708.34   |       -4388.24   |       -320.108   |    0.004229314   |      0.4746448   |       16.82107   |   03:05:48   |   00:19:57   |
18070       |       -4729.66   |        -4403.2   |        -326.46   |    0.004352673   |      -0.463784   |       16.82107   |   03:05:54   |   00:19:51   |
18080       |       -4730.94   |        -4405.1   |       -325.848   |    0.004868942   |      0.4574474   |       16.82107   |   03:06:02   |   00:19:45   |
18090       |       -4713.12   |       -4390.88   |       -322.238   |    0.004518358   |      0.2998793   |       16.82107   |   03:06:08   |   00:19:39   |
18100       |        -4698.5   |       -4380.61   |       -317.888   |    0.004448398   |      -1.045819   |       16.82107   |   03:06:15   |   00:19:33   |
18110       |       -4701.22   |          -4382   |       -319.222   |    0.004649717   |     -0.9143193   |       16.82107   |   03:06:21   |   00:19:26   |
18120       |       -4735.82   |       -4407.21   | 

18530       |       -4706.22   |       -4385.04   |       -321.179   |    0.004394889   |     -0.6212756   |       16.82107   |   03:10:47   |   00:15:08   |
18540       |        -4711.6   |       -4396.06   |       -315.539   |    0.004500746   |       0.310036   |       16.82107   |   03:10:53   |   00:15:01   |
18550       |       -4711.73   |       -4394.08   |       -317.653   |    0.004124311   |      0.4562545   |       16.82107   |   03:10:59   |   00:14:55   |
18560       |       -4719.15   |       -4396.72   |       -322.423   |    0.003962475   |        0.58198   |       16.82107   |   03:11:05   |   00:14:49   |
18570       |       -4705.27   |       -4385.41   |       -319.861   |    0.004914915   |      0.7153655   |       16.82107   |   03:11:11   |   00:14:43   |
18580       |       -4709.68   |       -4390.87   |       -318.812   |     0.00436076   |       1.083792   |       16.82107   |   03:11:17   |   00:14:37   |
18590       |       -4709.17   |       -4388.66   | 

Iter        |      Posterior   |     Likelihood   |          Prior   |   branch_rates   |   diversific..   |    extant_mrca   |    elapsed   |        ETA   |
-------------------------------------------------------------------------------------------------------------------------------------------------------------
19000       |       -4717.28   |       -4395.27   |        -322.01   |    0.004251154   |      0.9635053   |       16.82107   |   03:15:51   |   00:10:18   |
19010       |       -4713.77   |       -4391.01   |        -322.76   |    0.004221551   |     -0.6377611   |       16.82107   |   03:15:57   |   00:10:12   |
19020       |       -4721.89   |       -4398.95   |       -322.944   |    0.003959737   |      -1.246785   |       16.82107   |   03:16:03   |   00:10:06   |
19030       |       -4702.99   |       -4381.32   |       -321.667   |    0.004712466   |       -1.07677   |       16.82107   |   03:16:10   |   00:09:59   |
19040       |       -4708.24   |       -4386.41   | 

19450       |       -4705.19   |       -4388.85   |       -316.339   |    0.005342029   |     -0.2965502   |       16.82107   |   03:20:30   |   00:05:40   |
19460       |       -4710.36   |       -4393.91   |       -316.453   |    0.004577891   |      0.7128551   |       16.82107   |   03:20:36   |   00:05:33   |
19470       |       -4716.99   |       -4391.89   |       -325.107   |    0.004276999   |      0.8235809   |       16.82107   |   03:20:42   |   00:05:27   |
19480       |       -4704.22   |       -4387.96   |       -316.264   |     0.00454496   |      0.6155394   |       16.82107   |   03:20:48   |   00:05:21   |
19490       |       -4696.14   |       -4378.73   |       -317.417   |    0.004326874   |       0.554429   |       16.82107   |   03:20:54   |   00:05:15   |
19500       |       -4699.18   |       -4381.62   |       -317.559   |    0.004387542   |     -0.4639352   |       16.82107   |   03:21:01   |   00:05:09   |
19510       |       -4701.55   |       -4381.72   | 

19920       |       -4702.57   |       -4387.61   |       -314.961   |    0.005301838   |     -0.1743346   |       16.82107   |   03:25:20   |   00:00:49   |
19930       |       -4699.46   |        -4381.8   |       -317.663   |    0.004341876   |     -0.9371565   |       16.82107   |   03:25:26   |   00:00:43   |
19940       |       -4704.88   |       -4383.94   |       -320.941   |    0.004739386   |      0.5612981   |       16.82107   |   03:25:32   |   00:00:37   |
19950       |       -4720.01   |       -4397.35   |       -322.656   |    0.004808851   |      -1.012287   |       16.82107   |   03:25:38   |   00:00:30   |
19960       |       -4737.38   |       -4404.29   |       -333.089   |    0.003561524   |     -0.6853425   |       16.82107   |   03:25:44   |   00:00:24   |
19970       |       -4726.34   |       -4404.19   |       -322.142   |    0.004710306   |        1.15886   |       16.82107   |   03:25:50   |   00:00:18   |
19980       |       -4712.08   |       -4392.21   | 